In [1]:
import folium
import pandas as pd
from bs4 import BeautifulSoup
#import pickle
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait  # for implicit and explict waits
from selenium.webdriver.chrome.options import Options  # for suppressing the browser

In [2]:
chrome_driver_path = 'C:\drivers\chromedriver.exe'
url = "https://m.le360.ma/covidmaroc/"
option = webdriver.ChromeOptions()
option.add_argument('headless')
browser = webdriver.Chrome(chrome_driver_path,options=option)
browser.get(url)
html = browser.page_source
browser.quit()

In [3]:
'''outfile = open('html_save','wb')
pickle.dump(html,outfile)
outfile.close()'''
'''infile = open('html_save','rb')
html = pickle.load(infile)
infile.close()'''

"infile = open('html_save','rb')\nhtml = pickle.load(infile)\ninfile.close()"

In [4]:
soup = BeautifulSoup(html,'html.parser')
list_table=soup.find_all('table', class_='table table-bordered dataTable')[0].find('tbody').find_all('tr')

In [5]:
mytable=[]
for row in list_table:
    row=row.find_all('td')
    
    name = row[0].text.split('\u200b')[0]
    cas = int(row[1].text)
    cast_24 = int(row[2].text[1:])
    if(row[3].text[1:]==''):
        dead_24=0
    else:
        dead_24 = int(row[3].text[1:])
    mytable.append({'name': name , 'cas': cas , 'cas_24': cast_24, 'dead_24':dead_24 })

In [6]:
regions_loc = [{'name': 'Oriental',
  'latitude': 34.21063161705621,
  'longitude': -2.2398292872475123},
 {'name': 'Tanger Tetouan Al Hoceima',
  'latitude': 35.21648916999964,
  'longitude': -5.46061811161441},
 {'name': 'Guelmim Oued Noun',
  'latitude': 28.537079417694862,
  'longitude': -10.21129615427537},
 {'name': 'Dakhla-Oued Ed Daha',
  'latitude': 23.187768662138904,
  'longitude': -14.576887039381933},
 {'name': 'Beni Mellal-Khénifra',
  'latitude': 32.35536866706775,
  'longitude': -6.354611221480209},
 {'name': 'Darâa-Tafilalet',
  'latitude': 30.849663419282095,
  'longitude': -5.281174310301617},
 {'name': 'Marrakech Safi',
  'latitude': 31.658566001930208,
  'longitude': -8.50060605705501},
 {'name': 'Grand Casablanca-Settat',
  'latitude': 33.09434328504623,
  'longitude': -7.5835225431320215},
 {'name': 'Fès meknes',
  'latitude': 33.81997585277711,
  'longitude': -4.635183604212562},
 {'name': 'Laâyoune-Sakia El Hamra',
  'latitude': 26.150695319294833,
  'longitude': -12.827810335977418},
 {'name': 'Rabat Salé Kenitra',
  'latitude': 34.03819378608868,
  'longitude': -6.373051694854541},
 {'name': 'Souss-Massa',
  'latitude': 29.911104363087805,
  'longitude': -8.683976891847944}]

In [7]:
L=[]
for i in range(12):
    for j in range(12):
        if(regions_loc[i]['name']==mytable[j]['name']):
            mytable[j]['latitude'] = regions_loc[i]['latitude']
            mytable[j]['longitude'] = regions_loc[i]['longitude']
            L.append(mytable[j])
            continue

In [8]:
df = pd.DataFrame(L)
df

name    cas  cas_24  dead_24   latitude  longitude
0                    Oriental   3470     158        2  34.210632  -2.239829
1   Tanger Tetouan Al Hoceima  12971      81        1  35.216489  -5.460618
2           Guelmim Oued Noun    776      32        0  28.537079 -10.211296
3         Dakhla-Oued Ed Daha   1899      15        0  23.187769 -14.576887
4        Beni Mellal-Khénifra   6484     169        5  32.355369  -6.354611
5             Darâa-Tafilalet   7578     150        5  30.849663  -5.281174
6              Marrakech Safi  16129     165        7  31.658566  -8.500606
7     Grand Casablanca-Settat  45775    1247        9  33.094343  -7.583523
8                  Fès meknes  11814      58        3  33.819976  -4.635184
9     Laâyoune-Sakia El Hamra   1626      21        0  26.150695 -12.827810
10         Rabat Salé Kenitra  13908     215        2  34.038194  -6.373052
11                Souss-Massa   6052     210        0  29.911104  -8.683977

In [9]:
ma = folium.Map(location=[30, -10], zoom_start=5, min_zoom=4, max_zoom=7,tiles="cartodbpositron")
geo = "https://raw.githubusercontent.com/Salah-Zkara/Morocco-GeoJson/master/Morocco-Regions.json"
folium.Choropleth(
    geo_data=geo,
    name='COVID-19',
    data=df,
    columns=['name', 'cas'],
    key_on='feature.properties.nom_region',
    fill_color='OrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Total de cas confirmé',
).add_to(ma)

In [10]:
def plotDot(point):
    html ="<center>"+str(point['name'])+"</center>"+"<br>"+"<font color='#d95e00'>"+"<b>"+str(point['cas'])+"</b>"+"</font>"+" Total de cas confirmé.<br>"+"<font color='#e6b01c'>"+"<b>"+str(point['cas_24'])+"</b>"+"</font>"+" Cas contaminés aujourd'hui.<br>"+"<font color='#cc0c0c'>"+"<b>"+str(point['dead_24'])+"</b>"+"</font>"+" Décès aujourd'hui.<br>"
    iframe = folium.IFrame(html,
                       width=250,
                       height=120)
    folium.CircleMarker(location=[point.latitude, point.longitude],
                        radius=24,
                        weight=0,
                        popup = folium.Popup(iframe),
                        fill_color='#000000',
                        fill_opacity=0,
                        line_opacity=0
                       ).add_to(ma)

df.apply(plotDot, axis = 1)

ma.fit_bounds(ma.get_bounds())

In [11]:
ma

In [12]:
ma.save(outfile= "Covid-Map-Morocco.html")